In [62]:
import argparse
import os
import numpy as np
import math

import torchvision.transforms as transforms
from torchvision.utils import save_image

from torch.utils.data import DataLoader
from torchvision import datasets
from torch.autograd import Variable

import torch.nn as nn
import torch.nn.functional as F
import torch

In [63]:
n_epochs = 100 # number of epochs of training
batch_size = 64 # size of batches
lr = 0.0002 # adam:learning rate
b1 = 0.5 # adam: decay of first order momentum of gradient
b2 = 0.999 # adam: decay of first order momentum of gradient
n_cpu = 8 # number of cpu threads to use during batch generation
latent_dim = 100 # dimensionality of the latent space
img_size = 28 # size of each image dimension
channels = 1 # number of image channels
sample_interval = 400 #interval between image samples
alpha_list = [0.1,0.5,1,2,10]

img_shape = (channels, img_size, img_size)
cuda = True if torch.cuda.is_available() else False
os.makedirs('images', exist_ok=True)
Tensor = torch.cuda.FloatTensor if cuda else torch.FloatTensor

In [64]:
# Configure data loader
os.makedirs('../../data/mnist', exist_ok=True)
dataloader = torch.utils.data.DataLoader(
    datasets.MNIST('../../data/mnist', train=True, download=True,
                   transform=transforms.Compose([
                       transforms.ToTensor(),
                       transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))
                   ])),
    batch_size=batch_size, shuffle=True)

In [65]:
d = 28*28
latent_dim = 3*28*28
class Generator(nn.Module):
    def __init__(self):
        super(Generator, self).__init__()

        def block(in_feat, out_feat, normalize=True):
            layers = [nn.Linear(in_feat, out_feat)]
            if normalize:
                layers.append(nn.BatchNorm1d(out_feat, 0.8))
            layers.append(nn.Tanh())
            return layers

        self.model = nn.Sequential(
            *block(latent_dim, d, normalize=False),
            *block(d, int(d/2)),
            
            nn.Linear(int(d/2), d),
            nn.Sigmoid()
        )

    def forward(self, X, M, Z):
        z = torch.cat((X, M, torch.mul(1-M,Z)), 1)
        z = z.view(X.size(0),-1)
        img = self.model(z)
        img = img.view(img.size(0), *img_shape)
        return img

In [66]:
class Discriminator(nn.Module):
    def __init__(self):
        super(Discriminator, self).__init__()

        self.model = nn.Sequential(
            nn.Linear(2*28*28, d),
            nn.Tanh(),
            nn.Linear(d, int(d/2)),
            nn.Tanh(),
            nn.Linear(int(d/2), d),
            nn.Sigmoid()
        )

    def forward(self, X_hat, H):
        img = torch.cat((X_hat, H),1)
        img = img.view(img.size(0),-1)
        mask = self.model(img)
        mask = mask.view(img.size(0), *img_shape)

        return mask

In [67]:
discriminator_loss = torch.nn.BCELoss()
generator_loss = torch.nn.BCELoss()
mask_loss = torch.nn.MSELoss()
# Initialize generator and discriminator
generator = Generator()
discriminator = Discriminator()

if cuda:
    generator.cuda()
    discriminator.cuda()
    discriminator_loss.cuda()

In [68]:
# Optimizers
optimizer_G = torch.optim.Adam(generator.parameters(), lr=lr, betas=(b1, b2))
optimizer_D = torch.optim.Adam(discriminator.parameters(), lr=lr, betas=(b1, b2))
# optimizer_G = torch.optim.SGD(generator.parameters(), lr = lr, momentum=0.9)
# optimizer_D = torch.optim.SGD(discriminator.parameters(), lr = lr, momentum=0.9)
Tensor = torch.cuda.FloatTensor if cuda else torch.FloatTensor

In [79]:
# ----------
#  Training
# ----------

for epoch in range(n_epochs):
    for i, (imgs, _) in enumerate(dataloader):

        
        # ----------------------------
        #  Discriminator optimization
        # ----------------------------
        
        optimizer_D.zero_grad()
        
        # draw kd examples from x_tilt, m
        M = torch.ones(imgs.size(), dtype = torch.float)
        dropout = nn.Dropout(p=0.5)
        M = dropout(M)/2      
        X_tilt = torch.mul(M, imgs) # size of X_tilt is [batch_size, 1, 28, 28]
        # draw kd of Z, B 
        Z = Variable(Tensor(np.random.normal(0, 1, imgs.size())))
        B = torch.ones(imgs.size(), dtype = torch.float)
        for n in range(imgs.size()[0]):
            for j in range(img_size):
                k = np.random.choice(28)
                B[n][0][j][k] = 0
        #X_bar = torch.rand_like(X_tilt)
       # X_hat = torch.rand_like(X_tilt)
        #H = torch.rand_like(M)
        d_loss = 0
        X_bar = generator(X_tilt, M, Z)
        
        X_hat = torch.mul(M,X_tilt) + torch.mul((1 - M),X_bar)
        gen_imgs = X_hat
        H = torch.mul(B, M) + 0.5*(1 - B)
        d_loss = discriminator_loss(torch.mul(discriminator(X_hat, H),1-B), torch.mul(M,1-B))        
        d_loss.backward()
        optimizer_D.step()     
        
        
        # -------------------------
        #  Generator optimization
        # -------------------------
        optimizer_G.zero_grad()
        alpha = 0.5
        
        M_prime = torch.zeros_like(M)
        X_bar = X_bar.detach()
        X_hat = torch.mul(M,X_tilt) + torch.mul((1 - M),X_bar)
        g_loss = generator_loss(torch.mul(discriminator(X_hat, H),1-B), M_prime)
        m_loss = mask_loss(torch.mul(X_bar, M), torch.mul(X_tilt, M))
        g_loss_total = g_loss + alpha*m_loss
        
        g_loss_total.backward()
        optimizer_G.step()
        
        

        print ("[Epoch %d/%d] [Batch %d/%d] [D loss: %f] [G loss: %f]" % (epoch, n_epochs, i, len(dataloader),
                                                            d_loss.item(), g_loss.item()))

        batches_done = epoch * len(dataloader) + i
        if batches_done % sample_interval == 0:
            save_image(gen_imgs.data[:25], 'images/%d.png' % batches_done, nrow=5, normalize=True)



[Epoch 0/100] [Batch 0/938] [D loss: 0.008832] [G loss: 0.074948]
[Epoch 0/100] [Batch 1/938] [D loss: 0.008708] [G loss: 0.072822]
[Epoch 0/100] [Batch 2/938] [D loss: 0.008876] [G loss: 0.076949]
[Epoch 0/100] [Batch 3/938] [D loss: 0.008853] [G loss: 0.077771]
[Epoch 0/100] [Batch 4/938] [D loss: 0.007873] [G loss: 0.078550]
[Epoch 0/100] [Batch 5/938] [D loss: 0.008738] [G loss: 0.075767]
[Epoch 0/100] [Batch 6/938] [D loss: 0.009274] [G loss: 0.077913]
[Epoch 0/100] [Batch 7/938] [D loss: 0.009216] [G loss: 0.076153]
[Epoch 0/100] [Batch 8/938] [D loss: 0.008230] [G loss: 0.078156]
[Epoch 0/100] [Batch 9/938] [D loss: 0.008601] [G loss: 0.078020]
[Epoch 0/100] [Batch 10/938] [D loss: 0.008433] [G loss: 0.078619]
[Epoch 0/100] [Batch 11/938] [D loss: 0.008430] [G loss: 0.075948]
[Epoch 0/100] [Batch 12/938] [D loss: 0.008118] [G loss: 0.079620]
[Epoch 0/100] [Batch 13/938] [D loss: 0.008395] [G loss: 0.079155]
[Epoch 0/100] [Batch 14/938] [D loss: 0.008857] [G loss: 0.076286]
[Epoc

[Epoch 0/100] [Batch 124/938] [D loss: 0.008658] [G loss: 0.076645]
[Epoch 0/100] [Batch 125/938] [D loss: 0.008529] [G loss: 0.077686]
[Epoch 0/100] [Batch 126/938] [D loss: 0.008328] [G loss: 0.077706]
[Epoch 0/100] [Batch 127/938] [D loss: 0.008686] [G loss: 0.073861]
[Epoch 0/100] [Batch 128/938] [D loss: 0.008709] [G loss: 0.083441]
[Epoch 0/100] [Batch 129/938] [D loss: 0.008690] [G loss: 0.077130]
[Epoch 0/100] [Batch 130/938] [D loss: 0.009113] [G loss: 0.074237]
[Epoch 0/100] [Batch 131/938] [D loss: 0.008267] [G loss: 0.075932]
[Epoch 0/100] [Batch 132/938] [D loss: 0.008105] [G loss: 0.072364]
[Epoch 0/100] [Batch 133/938] [D loss: 0.008436] [G loss: 0.077870]
[Epoch 0/100] [Batch 134/938] [D loss: 0.008933] [G loss: 0.076109]
[Epoch 0/100] [Batch 135/938] [D loss: 0.008299] [G loss: 0.073883]
[Epoch 0/100] [Batch 136/938] [D loss: 0.008886] [G loss: 0.073899]
[Epoch 0/100] [Batch 137/938] [D loss: 0.008484] [G loss: 0.073581]
[Epoch 0/100] [Batch 138/938] [D loss: 0.008140]

[Epoch 0/100] [Batch 246/938] [D loss: 0.008454] [G loss: 0.077212]
[Epoch 0/100] [Batch 247/938] [D loss: 0.009087] [G loss: 0.076112]
[Epoch 0/100] [Batch 248/938] [D loss: 0.008294] [G loss: 0.078629]
[Epoch 0/100] [Batch 249/938] [D loss: 0.008567] [G loss: 0.080937]
[Epoch 0/100] [Batch 250/938] [D loss: 0.008282] [G loss: 0.076539]
[Epoch 0/100] [Batch 251/938] [D loss: 0.008530] [G loss: 0.079049]
[Epoch 0/100] [Batch 252/938] [D loss: 0.008051] [G loss: 0.079674]
[Epoch 0/100] [Batch 253/938] [D loss: 0.008416] [G loss: 0.076662]
[Epoch 0/100] [Batch 254/938] [D loss: 0.008698] [G loss: 0.076047]
[Epoch 0/100] [Batch 255/938] [D loss: 0.009005] [G loss: 0.077214]
[Epoch 0/100] [Batch 256/938] [D loss: 0.008608] [G loss: 0.074181]
[Epoch 0/100] [Batch 257/938] [D loss: 0.009356] [G loss: 0.080235]
[Epoch 0/100] [Batch 258/938] [D loss: 0.008810] [G loss: 0.076442]
[Epoch 0/100] [Batch 259/938] [D loss: 0.008368] [G loss: 0.074248]
[Epoch 0/100] [Batch 260/938] [D loss: 0.008805]

[Epoch 0/100] [Batch 368/938] [D loss: 0.008513] [G loss: 0.080312]
[Epoch 0/100] [Batch 369/938] [D loss: 0.008625] [G loss: 0.078013]
[Epoch 0/100] [Batch 370/938] [D loss: 0.009030] [G loss: 0.078639]
[Epoch 0/100] [Batch 371/938] [D loss: 0.008524] [G loss: 0.081015]
[Epoch 0/100] [Batch 372/938] [D loss: 0.008277] [G loss: 0.079606]
[Epoch 0/100] [Batch 373/938] [D loss: 0.008221] [G loss: 0.077957]
[Epoch 0/100] [Batch 374/938] [D loss: 0.008482] [G loss: 0.074672]
[Epoch 0/100] [Batch 375/938] [D loss: 0.008898] [G loss: 0.074890]
[Epoch 0/100] [Batch 376/938] [D loss: 0.009229] [G loss: 0.078908]
[Epoch 0/100] [Batch 377/938] [D loss: 0.008423] [G loss: 0.078921]
[Epoch 0/100] [Batch 378/938] [D loss: 0.008441] [G loss: 0.074671]
[Epoch 0/100] [Batch 379/938] [D loss: 0.008198] [G loss: 0.077159]
[Epoch 0/100] [Batch 380/938] [D loss: 0.008180] [G loss: 0.078171]
[Epoch 0/100] [Batch 381/938] [D loss: 0.008134] [G loss: 0.080831]
[Epoch 0/100] [Batch 382/938] [D loss: 0.008929]

[Epoch 0/100] [Batch 490/938] [D loss: 0.008647] [G loss: 0.076225]
[Epoch 0/100] [Batch 491/938] [D loss: 0.009226] [G loss: 0.075043]
[Epoch 0/100] [Batch 492/938] [D loss: 0.008627] [G loss: 0.078939]
[Epoch 0/100] [Batch 493/938] [D loss: 0.009265] [G loss: 0.073646]
[Epoch 0/100] [Batch 494/938] [D loss: 0.007836] [G loss: 0.080095]
[Epoch 0/100] [Batch 495/938] [D loss: 0.008587] [G loss: 0.074642]
[Epoch 0/100] [Batch 496/938] [D loss: 0.008537] [G loss: 0.082894]
[Epoch 0/100] [Batch 497/938] [D loss: 0.008442] [G loss: 0.077484]
[Epoch 0/100] [Batch 498/938] [D loss: 0.008472] [G loss: 0.078832]
[Epoch 0/100] [Batch 499/938] [D loss: 0.009080] [G loss: 0.079261]
[Epoch 0/100] [Batch 500/938] [D loss: 0.008767] [G loss: 0.079577]
[Epoch 0/100] [Batch 501/938] [D loss: 0.008655] [G loss: 0.079387]
[Epoch 0/100] [Batch 502/938] [D loss: 0.008285] [G loss: 0.079871]
[Epoch 0/100] [Batch 503/938] [D loss: 0.008498] [G loss: 0.078173]
[Epoch 0/100] [Batch 504/938] [D loss: 0.008862]

...

[Epoch 66/100] [Batch 791/938] [D loss: 0.008006] [G loss: 0.099468]
[Epoch 66/100] [Batch 792/938] [D loss: 0.007861] [G loss: 0.096845]
[Epoch 66/100] [Batch 793/938] [D loss: 0.007251] [G loss: 0.094504]
[Epoch 66/100] [Batch 794/938] [D loss: 0.008187] [G loss: 0.091942]
[Epoch 66/100] [Batch 795/938] [D loss: 0.007980] [G loss: 0.097910]
[Epoch 66/100] [Batch 796/938] [D loss: 0.007273] [G loss: 0.099847]
[Epoch 66/100] [Batch 797/938] [D loss: 0.007956] [G loss: 0.098282]
[Epoch 66/100] [Batch 798/938] [D loss: 0.007163] [G loss: 0.099668]
[Epoch 66/100] [Batch 799/938] [D loss: 0.007610] [G loss: 0.100387]
[Epoch 66/100] [Batch 800/938] [D loss: 0.007708] [G loss: 0.091719]
[Epoch 66/100] [Batch 801/938] [D loss: 0.008013] [G loss: 0.097502]
[Epoch 66/100] [Batch 802/938] [D loss: 0.008115] [G loss: 0.095766]
[Epoch 66/100] [Batch 803/938] [D loss: 0.007443] [G loss: 0.100583]
[Epoch 66/100] [Batch 804/938] [D loss: 0.008193] [G loss: 0.100160]
[Epoch 66/100] [Batch 805/938] [D 

[Epoch 66/100] [Batch 911/938] [D loss: 0.007761] [G loss: 0.099884]
[Epoch 66/100] [Batch 912/938] [D loss: 0.007570] [G loss: 0.096267]
[Epoch 66/100] [Batch 913/938] [D loss: 0.007892] [G loss: 0.097213]
[Epoch 66/100] [Batch 914/938] [D loss: 0.008983] [G loss: 0.097187]
[Epoch 66/100] [Batch 915/938] [D loss: 0.007457] [G loss: 0.098084]
[Epoch 66/100] [Batch 916/938] [D loss: 0.007996] [G loss: 0.093384]
[Epoch 66/100] [Batch 917/938] [D loss: 0.008047] [G loss: 0.095526]
[Epoch 66/100] [Batch 918/938] [D loss: 0.008206] [G loss: 0.096675]
[Epoch 66/100] [Batch 919/938] [D loss: 0.008081] [G loss: 0.101945]
[Epoch 66/100] [Batch 920/938] [D loss: 0.008001] [G loss: 0.098485]
[Epoch 66/100] [Batch 921/938] [D loss: 0.008063] [G loss: 0.093574]
[Epoch 66/100] [Batch 922/938] [D loss: 0.007693] [G loss: 0.101469]
[Epoch 66/100] [Batch 923/938] [D loss: 0.007862] [G loss: 0.096965]
[Epoch 66/100] [Batch 924/938] [D loss: 0.007641] [G loss: 0.102167]
[Epoch 66/100] [Batch 925/938] [D 

[Epoch 67/100] [Batch 95/938] [D loss: 0.007920] [G loss: 0.102585]
[Epoch 67/100] [Batch 96/938] [D loss: 0.007002] [G loss: 0.100370]
[Epoch 67/100] [Batch 97/938] [D loss: 0.007345] [G loss: 0.101161]
[Epoch 67/100] [Batch 98/938] [D loss: 0.008466] [G loss: 0.097570]
[Epoch 67/100] [Batch 99/938] [D loss: 0.007547] [G loss: 0.097498]
[Epoch 67/100] [Batch 100/938] [D loss: 0.008139] [G loss: 0.097196]
[Epoch 67/100] [Batch 101/938] [D loss: 0.008494] [G loss: 0.101146]
[Epoch 67/100] [Batch 102/938] [D loss: 0.007717] [G loss: 0.099505]
[Epoch 67/100] [Batch 103/938] [D loss: 0.007582] [G loss: 0.095070]
[Epoch 67/100] [Batch 104/938] [D loss: 0.007665] [G loss: 0.093795]
[Epoch 67/100] [Batch 105/938] [D loss: 0.007910] [G loss: 0.100228]
[Epoch 67/100] [Batch 106/938] [D loss: 0.007677] [G loss: 0.099381]
[Epoch 67/100] [Batch 107/938] [D loss: 0.008893] [G loss: 0.094479]
[Epoch 67/100] [Batch 108/938] [D loss: 0.007925] [G loss: 0.099361]
[Epoch 67/100] [Batch 109/938] [D loss:

[Epoch 67/100] [Batch 215/938] [D loss: 0.008143] [G loss: 0.100442]
[Epoch 67/100] [Batch 216/938] [D loss: 0.007891] [G loss: 0.092025]
[Epoch 67/100] [Batch 217/938] [D loss: 0.008366] [G loss: 0.099104]
[Epoch 67/100] [Batch 218/938] [D loss: 0.007316] [G loss: 0.096792]
[Epoch 67/100] [Batch 219/938] [D loss: 0.007631] [G loss: 0.098895]
[Epoch 67/100] [Batch 220/938] [D loss: 0.007506] [G loss: 0.097884]
[Epoch 67/100] [Batch 221/938] [D loss: 0.007232] [G loss: 0.101291]
[Epoch 67/100] [Batch 222/938] [D loss: 0.007121] [G loss: 0.100089]
[Epoch 67/100] [Batch 223/938] [D loss: 0.007674] [G loss: 0.097833]
[Epoch 67/100] [Batch 224/938] [D loss: 0.007988] [G loss: 0.094203]
[Epoch 67/100] [Batch 225/938] [D loss: 0.006884] [G loss: 0.098114]
[Epoch 67/100] [Batch 226/938] [D loss: 0.007212] [G loss: 0.101652]
[Epoch 67/100] [Batch 227/938] [D loss: 0.007736] [G loss: 0.101317]
[Epoch 67/100] [Batch 228/938] [D loss: 0.007868] [G loss: 0.094847]
[Epoch 67/100] [Batch 229/938] [D 

KeyboardInterrupt: 